# Airfare and Traffic Data Analysis

In [3]:
# Import required libraries
import streamlit as st
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
import 

## Importing Dataset

** Table 6 is the table from USDoT.
** The dropped columns were keys or other info useful when working with other tables, but not in this project.
** The two city columns create a city-pair, which is used to provide info on the number of passengers and fares between the pair.

In [6]:
drop_cols = ['tbl', 'citymarketid_1', 'citymarketid_2', 'table_1_flag', 'tbl6pk', 'Geocoded_City1', 'Geocoded_City2']
df = pd.read_csv('..\Consumer_Airfare_Report__Table_6_-_Contiguous_State_City-Pair_Markets_That_Average_At_Least_10_Passengers_Per_Day.csv',
                 usecols=(lambda x: x not in drop_cols)
                 )
carriers_df = pd.read_csv('..\\carrier_codes.csv') # The airline carrier codes list from DoT

df.head()

Year  quarter                           city1  \
0  2004        2               Oklahoma City, OK   
1  2003        2                   Nashville, TN   
2  2004        4                     Lincoln, NE   
3  2004        2                 Kansas City, MO   
4  2003        2  Allentown/Bethlehem/Easton, PA   

                              city2  nsmiles  passengers    fare carrier_lg  \
0    West Palm Beach/Palm Beach, FL     1197          11  242.51         DL   
1    West Palm Beach/Palm Beach, FL      758         138  136.00         WN   
2                     San Diego, CA     1259          19  193.88         UA   
3  Wausau/Mosinee/Stevens Point, WI      459          13  199.57         NW   
4                        Denver, CO     1539          29  272.83         UA   

   large_ms  fare_lg carrier_low  lf_ms  fare_low  
0      0.51   235.98          DL   0.51    235.98  
1      0.73   126.54          WN   0.73    126.54  
2      0.84   194.65          NW   0.13    176.53  
3      0.70   201.34          UA   0.13    195.58  
4      0.32   321.47          DL   0.17    201.91

In [51]:
df.rename(columns=str.lower, inplace=True)
df.rename(columns={
    'nsmiles': 'nonstop_miles',
    'carrier_lg': 'carrier_largest',
    'large_ms': 'market_share_largest',
    'fare_lg': 'fare_largest',
    'carrier_low': 'carrier_lowfare',
    'lf_ms': 'market_share_lowfare',
    'fare_low': 'fare_lowfare'
    },
    inplace=True)

df['city-pair'] = df['city1'] + " - " + df['city2']
df.info()
df.head()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 581690 entries, 0 to 581689
Data columns (total 20 columns):
 #   Column                Non-Null Count   Dtype  
---  ------                --------------   -----  
 0   year                  581690 non-null  int64  
 1   quarter               581690 non-null  int64  
 2   city1                 581690 non-null  object 
 3   city2                 581690 non-null  object 
 4   nonstop_miles         581690 non-null  int64  
 5   passengers            581690 non-null  int64  
 6   fare                  581690 non-null  float64
 7   carrier_largest       581690 non-null  object 
 8   market_share_largest  581690 non-null  float64
 9   fare_largest          581690 non-null  float64
 10  carrier_lowfare       581690 non-null  object 
 11  market_share_lowfare  581690 non-null  float64
 12  fare_lowfare          581690 non-null  float64
 13  city1_lat             581690 non-null  float64
 14  city1_lon             581690 non-null  float64
 15  

year  quarter                           city1  \
0  2004        2               Oklahoma City, OK   
1  2003        2                   Nashville, TN   
2  2004        4                     Lincoln, NE   
3  2004        2                 Kansas City, MO   
4  2003        2  Allentown/Bethlehem/Easton, PA   

                              city2  nonstop_miles  passengers    fare  \
0    West Palm Beach/Palm Beach, FL           1197          11  242.51   
1    West Palm Beach/Palm Beach, FL            758         138  136.00   
2                     San Diego, CA           1259          19  193.88   
3  Wausau/Mosinee/Stevens Point, WI            459          13  199.57   
4                        Denver, CO           1539          29  272.83   

  carrier_largest  market_share_largest  fare_largest carrier_lowfare  \
0              DL                  0.51        235.98              DL   
1              WN                  0.73        126.54              WN   
2              UA                  0.84        194.65              NW   
3              NW                  0.70        201.34              UA   
4              UA                  0.32        321.47              DL   

   market_share_lowfare  fare_lowfare  city1_lat  city1_lon  city2_lat  \
0                  0.51        235.98  35.472989 -97.517054  26.715364   
1                  0.73        126.54  36.162277 -86.774298  26.715364   
2                  0.13        176.53  40.808886 -96.707775  32.717420   
3                  0.13        195.58  39.100105 -94.578142  44.522922   
4                  0.17        201.91  40.688493 -75.216982  39.739236   

    city2_lon          airline_largest          airline_lowfare  \
0  -80.053294     Delta Air Lines Inc.     Delta Air Lines Inc.   
1  -80.053294   Southwest Airlines Co.   Southwest Airlines Co.   
2 -117.162773    United Air Lines Inc.  Northwest Airlines Inc.   
3  -89.574111  Northwest Airlines Inc.    United Air Lines Inc.   
4 -104.984862    United Air Lines Inc.     Delta Air Lines Inc.   

                                           city-pair  
0  Oklahoma City, OK - West Palm Beach/Palm Beach...  
1     Nashville, TN - West Palm Beach/Palm Beach, FL  
2                        Lincoln, NE - San Diego, CA  
3  Kansas City, MO - Wausau/Mosinee/Stevens Point...  
4        Allentown/Bethlehem/Easton, PA - Denver, CO

### Fixing missing values and nulls

In [52]:
missing_df = df[df['carrier_largest'].isna()]
missing_df.head()

Empty DataFrame
Columns: [year, quarter, city1, city2, nonstop_miles, passengers, fare, carrier_largest, market_share_largest, fare_largest, carrier_lowfare, market_share_lowfare, fare_lowfare, city1_lat, city1_lon, city2_lat, city2_lon, airline_largest, airline_lowfare, city-pair]
Index: []

In [53]:
missing_df.describe()

year  quarter  nonstop_miles  passengers  fare  market_share_largest  \
count   0.0      0.0            0.0         0.0   0.0                   0.0   
mean    NaN      NaN            NaN         NaN   NaN                   NaN   
std     NaN      NaN            NaN         NaN   NaN                   NaN   
min     NaN      NaN            NaN         NaN   NaN                   NaN   
25%     NaN      NaN            NaN         NaN   NaN                   NaN   
50%     NaN      NaN            NaN         NaN   NaN                   NaN   
75%     NaN      NaN            NaN         NaN   NaN                   NaN   
max     NaN      NaN            NaN         NaN   NaN                   NaN   

       fare_largest  market_share_lowfare  fare_lowfare  city1_lat  city1_lon  \
count           0.0                   0.0           0.0        0.0        0.0   
mean            NaN                   NaN           NaN        NaN        NaN   
std             NaN                   NaN           NaN        NaN        NaN   
min             NaN                   NaN           NaN        NaN        NaN   
25%             NaN                   NaN           NaN        NaN        NaN   
50%             NaN                   NaN           NaN        NaN        NaN   
75%             NaN                   NaN           NaN        NaN        NaN   
max             NaN                   NaN           NaN        NaN        NaN   

       city2_lat  city2_lon  
count        0.0        0.0  
mean         NaN        NaN  
std          NaN        NaN  
min          NaN        NaN  
25%          NaN        NaN  
50%          NaN        NaN  
75%          NaN        NaN  
max          NaN        NaN

There are a number of rows that don't have market share data at all. Those rows will be deleted. The rows that have a market share leader but no lowest fare data will be preserved by adding the largest carrier as the lowest fare carrier.  This is a small number of entries that will not adversely affect the analysis.

In [54]:
# 
df = df.dropna(subset=['carrier_largest'])
df = df.reset_index(drop=True)

df.carrier_lowfare.fillna(df.carrier_largest, inplace=True)
df.market_share_lowfare.fillna(df.market_share_largest, inplace=True)
df.fare_lowfare.fillna(df.fare_largest, inplace=True)

df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 581690 entries, 0 to 581689
Data columns (total 20 columns):
 #   Column                Non-Null Count   Dtype  
---  ------                --------------   -----  
 0   year                  581690 non-null  int64  
 1   quarter               581690 non-null  int64  
 2   city1                 581690 non-null  object 
 3   city2                 581690 non-null  object 
 4   nonstop_miles         581690 non-null  int64  
 5   passengers            581690 non-null  int64  
 6   fare                  581690 non-null  float64
 7   carrier_largest       581690 non-null  object 
 8   market_share_largest  581690 non-null  float64
 9   fare_largest          581690 non-null  float64
 10  carrier_lowfare       581690 non-null  object 
 11  market_share_lowfare  581690 non-null  float64
 12  fare_lowfare          581690 non-null  float64
 13  city1_lat             581690 non-null  float64
 14  city1_lon             581690 non-null  float64
 15  

## Geocoding and Decoding Carrier Codes

The geocoding in the dataset was a mess. It was implemented only in certain years, and the format was not uniform. The following will export a cities list to query outside sources for geocoding.

In [55]:
# Query the df for a list of cities to be geocoded.
city_df = pd.DataFrame(np.unique(df[['city1','city2']].values),columns=['address'])
city_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 376 entries, 0 to 375
Data columns (total 1 columns):
 #   Column   Non-Null Count  Dtype 
---  ------   --------------  ----- 
 0   address  376 non-null    object
dtypes: object(1)
memory usage: 3.1+ KB


In [18]:
city_df.to_csv('..\\cities.csv')

In [37]:
coords_df = pd.read_csv('..\\city_locations.csv')  # imported geocode mostly from geocod.io

In [40]:
coords_df.info()
coords_df.head()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 376 entries, 0 to 375
Data columns (total 3 columns):
 #   Column   Non-Null Count  Dtype  
---  ------   --------------  -----  
 0   address  376 non-null    object 
 1   lat      376 non-null    float64
 2   lon      376 non-null    float64
dtypes: float64(2), object(1)
memory usage: 8.9+ KB


address        lat         lon
0     Aberdeen, SD  45.464981  -98.487813
1      Abilene, TX  32.446450  -99.747591
2       Albany, GA  31.578206  -84.155681
3       Albany, NY  42.651167  -73.754968
4  Albuquerque, NM  35.084103 -106.650985

In [41]:
# Two left joins to incorporate geocode to the two city columns
df = df.merge(coords_df, left_on='city1', right_on='address', how='left')
df.rename(columns={'lat': 'city1_lat', 'lon': 'city1_lon'}, inplace=True)
df.drop(['address'], axis=1, inplace=True)

df = df.merge(coords_df, left_on='city2', right_on='address', how='left')
df.rename(columns={'lat': 'city2_lat', 'lon': 'city2_lon'}, inplace=True)
df.drop(['address'], axis=1, inplace=True)

df.info()
df.head(10)

<class 'pandas.core.frame.DataFrame'>
Int64Index: 581690 entries, 0 to 581689
Data columns (total 17 columns):
 #   Column                Non-Null Count   Dtype  
---  ------                --------------   -----  
 0   year                  581690 non-null  int64  
 1   quarter               581690 non-null  int64  
 2   city1                 581690 non-null  object 
 3   city2                 581690 non-null  object 
 4   nonstop_miles         581690 non-null  int64  
 5   passengers            581690 non-null  int64  
 6   fare                  581690 non-null  float64
 7   carrier_largest       581690 non-null  object 
 8   market_share_largest  581690 non-null  float64
 9   fare_largest          581690 non-null  float64
 10  carrier_lowfare       581690 non-null  object 
 11  market_share_lowfare  581690 non-null  float64
 12  fare_lowfare          581690 non-null  float64
 13  city1_lat             581690 non-null  float64
 14  city1_lon             581690 non-null  float64
 15  

year  quarter                           city1  \
0  2004        2               Oklahoma City, OK   
1  2003        2                   Nashville, TN   
2  2004        4                     Lincoln, NE   
3  2004        2                 Kansas City, MO   
4  2003        2  Allentown/Bethlehem/Easton, PA   
5  2009        2   Miami, FL (Metropolitan Area)   
6  2008        4              Raleigh/Durham, NC   
7  2004        3                   Charlotte, NC   
8  2003        3                      Denver, CO   
9  2013        2        Minneapolis/St. Paul, MN   

                              city2  nonstop_miles  passengers    fare  \
0    West Palm Beach/Palm Beach, FL           1197          11  242.51   
1    West Palm Beach/Palm Beach, FL            758         138  136.00   
2                     San Diego, CA           1259          19  193.88   
3  Wausau/Mosinee/Stevens Point, WI            459          13  199.57   
4                        Denver, CO           1539          29  272.83   
5                     Rochester, NY           1204         203  151.46   
6            Sarasota/Bradenton, FL            625          24  165.17   
7                     Knoxville, TN            177          11  308.14   
8                       Roanoke, VA           1344          21  237.31   
9                      Savannah, GA           1092         103  222.88   

  carrier_largest  market_share_largest  fare_largest carrier_lowfare  \
0              DL                  0.51        235.98              DL   
1              WN                  0.73        126.54              WN   
2              UA                  0.84        194.65              NW   
3              NW                  0.70        201.34              UA   
4              UA                  0.32        321.47              DL   
5              FL                  0.29        131.05              FL   
6              DL                  0.47        165.67              FL   
7              US                  0.94        310.41              DL   
8              UA                  0.38        267.44              NW   
9              DL                  0.70        224.80              UA   

   market_share_lowfare  fare_lowfare  city1_lat   city1_lon  city2_lat  \
0                  0.51        235.98  35.472989  -97.517054  26.715364   
1                  0.73        126.54  36.162277  -86.774298  26.715364   
2                  0.13        176.53  40.808886  -96.707775  32.717420   
3                  0.13        195.58  39.100105  -94.578142  44.522922   
4                  0.17        201.91  40.688493  -75.216982  39.739236   
5                  0.29        131.05  25.766368  -80.210268  43.157285   
6                  0.21        154.50  35.906111  -78.995782  27.491923   
7                  0.02        151.90  35.227209  -80.843083  35.960395   
8                  0.11        155.75  39.739236 -104.984862  37.270973   
9                  0.13        175.85  44.922705  -93.055492  32.056457   

    city2_lon  
0  -80.053294  
1  -80.053294  
2 -117.162773  
3  -89.574111  
4 -104.984862  
5  -77.615214  
6  -82.580770  
7  -83.921026  
8  -79.941431  
9  -81.095127

In [44]:
df.carrier_largest.nunique(), df.carrier_lowfare.nunique()

(56, 70)

In [46]:
carriers_df.rename(columns=str.lower, inplace=True)
carriers_df.info()


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1655 entries, 0 to 1654
Data columns (total 2 columns):
 #   Column   Non-Null Count  Dtype 
---  ------   --------------  ----- 
 0   code     1654 non-null   object
 1   airline  1655 non-null   object
dtypes: object(2)
memory usage: 26.0+ KB


In [47]:
carriers_df.head()

code                        airline
0  02Q                  Titan Airways
1  04Q             Tradewind Aviation
2  05Q            Comlux Aviation, AG
3  06Q  Master Top Linhas Aereas Ltd.
4  07Q            Flair Airlines Ltd.

In [48]:
# Two more left joins to add the names of the carriers to the df
df = df.merge(carriers_df, left_on='carrier_largest', right_on='code', how='left')
df.rename(columns={'airline': 'airline_largest'}, inplace=True)
df.drop(['code'], axis=1, inplace=True)

df = df.merge(carriers_df, left_on='carrier_lowfare', right_on='code', how='left')
df.rename(columns={'airline': 'airline_lowfare'}, inplace=True)
df.drop(['code'], axis=1, inplace=True)

In [49]:
df.head(10)

year  quarter                           city1  \
0  2004        2               Oklahoma City, OK   
1  2003        2                   Nashville, TN   
2  2004        4                     Lincoln, NE   
3  2004        2                 Kansas City, MO   
4  2003        2  Allentown/Bethlehem/Easton, PA   
5  2009        2   Miami, FL (Metropolitan Area)   
6  2008        4              Raleigh/Durham, NC   
7  2004        3                   Charlotte, NC   
8  2003        3                      Denver, CO   
9  2013        2        Minneapolis/St. Paul, MN   

                              city2  nonstop_miles  passengers    fare  \
0    West Palm Beach/Palm Beach, FL           1197          11  242.51   
1    West Palm Beach/Palm Beach, FL            758         138  136.00   
2                     San Diego, CA           1259          19  193.88   
3  Wausau/Mosinee/Stevens Point, WI            459          13  199.57   
4                        Denver, CO           1539          29  272.83   
5                     Rochester, NY           1204         203  151.46   
6            Sarasota/Bradenton, FL            625          24  165.17   
7                     Knoxville, TN            177          11  308.14   
8                       Roanoke, VA           1344          21  237.31   
9                      Savannah, GA           1092         103  222.88   

  carrier_largest  market_share_largest  fare_largest carrier_lowfare  \
0              DL                  0.51        235.98              DL   
1              WN                  0.73        126.54              WN   
2              UA                  0.84        194.65              NW   
3              NW                  0.70        201.34              UA   
4              UA                  0.32        321.47              DL   
5              FL                  0.29        131.05              FL   
6              DL                  0.47        165.67              FL   
7              US                  0.94        310.41              DL   
8              UA                  0.38        267.44              NW   
9              DL                  0.70        224.80              UA   

   market_share_lowfare  fare_lowfare  city1_lat   city1_lon  city2_lat  \
0                  0.51        235.98  35.472989  -97.517054  26.715364   
1                  0.73        126.54  36.162277  -86.774298  26.715364   
2                  0.13        176.53  40.808886  -96.707775  32.717420   
3                  0.13        195.58  39.100105  -94.578142  44.522922   
4                  0.17        201.91  40.688493  -75.216982  39.739236   
5                  0.29        131.05  25.766368  -80.210268  43.157285   
6                  0.21        154.50  35.906111  -78.995782  27.491923   
7                  0.02        151.90  35.227209  -80.843083  35.960395   
8                  0.11        155.75  39.739236 -104.984862  37.270973   
9                  0.13        175.85  44.922705  -93.055492  32.056457   

    city2_lon              airline_largest              airline_lowfare  
0  -80.053294         Delta Air Lines Inc.         Delta Air Lines Inc.  
1  -80.053294       Southwest Airlines Co.       Southwest Airlines Co.  
2 -117.162773        United Air Lines Inc.      Northwest Airlines Inc.  
3  -89.574111      Northwest Airlines Inc.        United Air Lines Inc.  
4 -104.984862        United Air Lines Inc.         Delta Air Lines Inc.  
5  -77.615214  AirTran Airways Corporation  AirTran Airways Corporation  
6  -82.580770         Delta Air Lines Inc.  AirTran Airways Corporation  
7  -83.921026              US Airways Inc.         Delta Air Lines Inc.  
8  -79.941431        United Air Lines Inc.      Northwest Airlines Inc.  
9  -81.095127         Delta Air Lines Inc.        United Air Lines Inc.

In [50]:
df.describe()

year        quarter  nonstop_miles     passengers  \
count  581690.000000  581690.000000  581690.000000  581690.000000   
mean     2009.021142       2.509393    1043.826349     179.120920   
std         7.671110       1.104600     586.179745     628.420943   
min      1996.000000       1.000000      46.000000      10.000000   
25%      2002.000000       2.000000     589.000000      17.000000   
50%      2009.000000       3.000000     918.000000      33.000000   
75%      2016.000000       3.000000    1401.000000      99.000000   
max      2022.000000       4.000000    2783.000000   25471.000000   

                fare  market_share_largest   fare_largest  \
count  581690.000000         581690.000000  581690.000000   
mean      232.461192              0.597529     232.999347   
std        70.457895              0.201048      75.422135   
min        50.450000              0.000900      50.450000   
25%       182.000000              0.440000     179.630000   
50%       229.360000              0.570000     229.640000   
75%       278.450000              0.740000     280.970000   
max       754.970000              1.000000    1366.950000   

       market_share_lowfare   fare_lowfare      city1_lat      city1_lon  \
count         581690.000000  581690.000000  581690.000000  581690.000000   
mean               0.387582     204.616347      37.456825     -91.378329   
std                0.277607      67.923241       5.293735      13.652916   
min                0.000900      50.000000      24.562557    -124.212652   
25%                0.160000     155.290000      33.695646     -97.743700   
50%                0.309000     200.180000      38.046407     -87.624421   
75%                0.565200     248.940000      41.875562     -81.690273   
max                1.000000    1366.950000      48.754401     -67.834909   

           city2_lat      city2_lon  
count  581690.000000  581690.000000  
mean       36.847805     -94.036642  
std         5.667024      15.941608  
min        24.562557    -124.212652  
25%        32.717420    -110.974848  
50%        37.538509     -90.051764  
75%        40.759620     -81.022833  
max        48.754401     -67.834909

In [18]:
# Uncomment to save processed file to repo
#df.to_csv(r'..\us_airfares_processed.csv')

## Questions to Answer:

* What city-pair was the busiest (top 20)? 
* What was the busiest airport each quarter?
* Pre-Covid vs Post-Covid -- Average ticket price? Passengers in top markets?

### 

### Top Routes Evaluated by Passenger Volume

In [56]:
pax_vol = df.groupby('city-pair').agg({'passengers':'mean'}).sort_values(by='passengers', ascending=False)

display(pax_vol)

fig = px.histogram(pax_vol, x='passengers')
fig.show()

passengers
city-pair                                                       
Los Angeles, CA (Metropolitan Area) - San Franc...  18506.261682
Miami, FL (Metropolitan Area) - New York City, ...  13559.495327
Los Angeles, CA (Metropolitan Area) - New York ...   9957.532710
New York City, NY (Metropolitan Area) - Orlando...   8780.897196
Chicago, IL - New York City, NY (Metropolitan A...   8719.943925
...                                                          ...
Columbus, GA - Minneapolis/St. Paul, MN                10.000000
Columbus, GA - El Paso, TX                             10.000000
Columbia, SC - Valparaiso, FL                          10.000000
Ashland, WV - New Orleans, LA                          10.000000
Lincoln, NE - Reno, NV                                 10.000000

[9573 rows x 1 columns]

### Miles vs Fares 

In [60]:
df['fare_per_mile'] = df.fare / df.nonstop_miles
# range_selection = st.slider('Select the time range for the plot:',
#                             df.year.min(),
#                             df.year.max(),
#                             (1999, 2013))
# flight_year_df = df[df['year'].between(range_selection[0],
#                                        range_selection[1], 
#                                        inclusive='both'
#                                       )]

flight_year_df = df[df.year == 2003]

fig_a = px.scatter(flight_year_df, 
                   x='nonstop_miles', 
                   y='fare',
                   trendline='ols', 
                   color='airline_largest', 
                   color_continuous_scale='speed')
fig_a.show()

### Geoplot Top Routes by Revenue

In [81]:
df['revenue'] = df['passengers'] * df['fare']

revenue_year = 2017
size_select = 100

revenue_df = df[df['year']==revenue_year].groupby('city-pair').agg({'revenue':'sum',
                                                                    'passengers':'sum',
                                                                    'airline_largest':lambda x:x.value_counts().index[0],
                                                                    'city1':'first',
                                                                    'city2':'first',
                                                                    'city1_lon':'first',
                                                                    'city2_lon':'first',
                                                                    'city1_lat':'first',
                                                                    'city2_lat':'first'})\
                                            .sort_values(by='revenue', ascending=False).head(size_select)



In [82]:
revenue_df

revenue  passengers  \
city-pair                                                                     
Los Angeles, CA (Metropolitan Area) - New York ...  19263013.30       51042   
New York City, NY (Metropolitan Area) - San Fra...  14309167.12       40227   
Los Angeles, CA (Metropolitan Area) - San Franc...  11348475.02       87549   
Miami, FL (Metropolitan Area) - New York City, ...  10337203.78       63334   
Chicago, IL - New York City, NY (Metropolitan A...   7954732.97       46361   
...                                                         ...         ...   
Boston, MA (Metropolitan Area) - Dallas/Fort Wo...   1782785.47        8292   
Dallas/Fort Worth, TX - Miami, FL (Metropolitan...   1778515.48        8280   
Denver, CO - Houston, TX                             1762383.71        8874   
Atlanta, GA (Metropolitan Area) - Las Vegas, NV      1753719.94        8138   
Dallas/Fort Worth, TX - Orlando, FL                  1727805.75        9309   

                                                           airline_largest  \
city-pair                                                                    
Los Angeles, CA (Metropolitan Area) - New York ...   United Air Lines Inc.   
New York City, NY (Metropolitan Area) - San Fra...   United Air Lines Inc.   
Los Angeles, CA (Metropolitan Area) - San Franc...  Southwest Airlines Co.   
Miami, FL (Metropolitan Area) - New York City, ...    Delta Air Lines Inc.   
Chicago, IL - New York City, NY (Metropolitan A...   United Air Lines Inc.   
...                                                                    ...   
Boston, MA (Metropolitan Area) - Dallas/Fort Wo...  American Airlines Inc.   
Dallas/Fort Worth, TX - Miami, FL (Metropolitan...  American Airlines Inc.   
Denver, CO - Houston, TX                            Southwest Airlines Co.   
Atlanta, GA (Metropolitan Area) - Las Vegas, NV       Delta Air Lines Inc.   
Dallas/Fort Worth, TX - Orlando, FL                 American Airlines Inc.   

                                                                                    city1  \
city-pair                                                                                   
Los Angeles, CA (Metropolitan Area) - New York ...    Los Angeles, CA (Metropolitan Area)   
New York City, NY (Metropolitan Area) - San Fra...  New York City, NY (Metropolitan Area)   
Los Angeles, CA (Metropolitan Area) - San Franc...    Los Angeles, CA (Metropolitan Area)   
Miami, FL (Metropolitan Area) - New York City, ...          Miami, FL (Metropolitan Area)   
Chicago, IL - New York City, NY (Metropolitan A...                            Chicago, IL   
...                                                                                   ...   
Boston, MA (Metropolitan Area) - Dallas/Fort Wo...         Boston, MA (Metropolitan Area)   
Dallas/Fort Worth, TX - Miami, FL (Metropolitan...                  Dallas/Fort Worth, TX   
Denver, CO - Houston, TX                                                       Denver, CO   
Atlanta, GA (Metropolitan Area) - Las Vegas, NV           Atlanta, GA (Metropolitan Area)   
Dallas/Fort Worth, TX - Orlando, FL                                 Dallas/Fort Worth, TX   

                                                                                    city2  \
city-pair                                                                                   
Los Angeles, CA (Metropolitan Area) - New York ...  New York City, NY (Metropolitan Area)   
New York City, NY (Metropolitan Area) - San Fra...  San Francisco, CA (Metropolitan Area)   
Los Angeles, CA (Metropolitan Area) - San Franc...  San Francisco, CA (Metropolitan Area)   
Miami, FL (Metropolitan Area) - New York City, ...  New York City, NY (Metropolitan Area)   
Chicago, IL - New York City, NY (Metropolitan A...  New York City, NY (Metropolitan Area)   
...                                                                                   ...   
Boston, MA (Metropolitan Area) - Dallas/Fort Wo...         

In [97]:
revenue_df[['passengers', 'revenue']]

passengers      revenue
city-pair                                                                  
Los Angeles, CA (Metropolitan Area) - New York ...       51042  19263013.30
New York City, NY (Metropolitan Area) - San Fra...       40227  14309167.12
Los Angeles, CA (Metropolitan Area) - San Franc...       87549  11348475.02
Miami, FL (Metropolitan Area) - New York City, ...       63334  10337203.78
Chicago, IL - New York City, NY (Metropolitan A...       46361   7954732.97
...                                                        ...          ...
Boston, MA (Metropolitan Area) - Dallas/Fort Wo...        8292   1782785.47
Dallas/Fort Worth, TX - Miami, FL (Metropolitan...        8280   1778515.48
Denver, CO - Houston, TX                                  8874   1762383.71
Atlanta, GA (Metropolitan Area) - Las Vegas, NV           8138   1753719.94
Dallas/Fort Worth, TX - Orlando, FL                       9309   1727805.75

[100 rows x 2 columns]

In [94]:
revenue_df.index.nunique()

100

In [85]:
plot_airports_df = revenue_df[['city1', 'city1_lon', 'city1_lat']]
plt_apts2 = revenue_df[['city2', 'city2_lon', 'city2_lat']]
plt_apts2.columns = plot_airports_df.columns
plot_airports_df = pd.concat([plot_airports_df, plt_apts2], axis=0)

plot_airports_df.head(10)

city1  \
city-pair                                                                                   
Los Angeles, CA (Metropolitan Area) - New York ...    Los Angeles, CA (Metropolitan Area)   
New York City, NY (Metropolitan Area) - San Fra...  New York City, NY (Metropolitan Area)   
Los Angeles, CA (Metropolitan Area) - San Franc...    Los Angeles, CA (Metropolitan Area)   
Miami, FL (Metropolitan Area) - New York City, ...          Miami, FL (Metropolitan Area)   
Chicago, IL - New York City, NY (Metropolitan A...                            Chicago, IL   
New York City, NY (Metropolitan Area) - Orlando...  New York City, NY (Metropolitan Area)   
Los Angeles, CA (Metropolitan Area) - Washingto...    Los Angeles, CA (Metropolitan Area)   
Atlanta, GA (Metropolitan Area) - New York City...        Atlanta, GA (Metropolitan Area)   
San Francisco, CA (Metropolitan Area) - Washing...  San Francisco, CA (Metropolitan Area)   
Chicago, IL - Los Angeles, CA (Metropolitan Area)                             Chicago, IL   

                                                     city1_lon  city1_lat  
city-pair                                                                  
Los Angeles, CA (Metropolitan Area) - New York ... -118.476863  33.995431  
New York City, NY (Metropolitan Area) - San Fra...  -74.002738  40.716649  
Los Angeles, CA (Metropolitan Area) - San Franc... -118.476863  33.995431  
Miami, FL (Metropolitan Area) - New York City, ...  -80.210268  25.766368  
Chicago, IL - New York City, NY (Metropolitan A...  -87.624421  41.875562  
New York City, NY (Metropolitan Area) - Orlando...  -74.002738  40.716649  
Los Angeles, CA (Metropolitan Area) - Washingto... -118.476863  33.995431  
Atlanta, GA (Metropolitan Area) - New York City...  -84.391906  33.758891  
San Francisco, CA (Metropolitan Area) - Washing... -122.419906  37.779026  
Chicago, IL - Los Angeles, CA (Metropolitan Area)   -87.624421  41.875562

In [87]:
fig_rev = go.Figure()

for i in range(len(revenue_df)):
    fig_rev.add_trace(
        go.Scattergeo(
            locationmode='USA-states',
            lon=[revenue_df['city1_lon'][i], revenue_df['city2_lon'][i]],
            lat=[revenue_df['city1_lat'][i], revenue_df['city2_lat'][i]],
            mode = 'lines',
            line = dict(width = 1,color = 'red'),
            opacity = float(i) / float(size_select)
        )
    )

In [89]:
fig_rev.add_trace(go.Scattergeo(
    #locationmode = "USA-states",
    lon = plot_airports_df['city1_lon'],
    lat = plot_airports_df['city1_lat'],
    hoverinfo= 'text',
    text = plot_airports_df['city1'],
    mode='markers',
    marker=dict(
            size = 5,
            color = 'rgb(255, 0, 0)',
            line = dict(
            width = 20,
            color = 'rgba(68, 68, 68, 0)'
            ),
    
    )))

In [90]:
fig_rev.update_layout(
    title_text = 'Biggest Markets in the USA by Revenue',
    title_x=0.4,
    title_y=0.9,
    showlegend = False,
    autosize = True,
    width=1200, height=720,    
    geo = dict(
        scope = 'north america',
        projection_type = 'azimuthal equal area',
        showland = True,
        landcolor = 'rgb(243, 243, 243)',
        countrycolor = 'rgb(204, 204, 204)'           
    ),
)
fig_rev.update_geos(fitbounds='locations')

In [91]:
fig_rev.show()